# **Dashboard Building**


#### Importing Libs and Loading Data

In [1]:
from dash import Dash, dcc, html, Input, Output, dash_table
import dash_bootstrap_components as dbc

import plotly.express as px

import pandas as pd

dash_data = pd.read_csv("../data/processed/3.0_dashboard_selection_kc_house_sales.csv")

In [2]:
dash_data.columns

Index(['price', 'bedrooms', 'bathrooms', 'floors', 'view', 'sqm_living15',
       'sqm_lot15', 'sqm_outdoor15', 'lot_living_ratio15', 'waterfront',
       'condition', 'grade', 'renovated', 'yr_built', 'age_of_house', 'city',
       'area_code', 'zipcode', 'dist_from_center', 'lat', 'long'],
      dtype='object')

#### Building Visualizations

In [3]:
#external_stylesheets = ['https://codepen.io/chriddyp/pen/bWLwgP.css']

In [393]:
kc_map = px.scatter_mapbox(
    data_frame=dash_data,
    lat='lat',
    lon='long',
    hover_name='city',
    hover_data={'lat': False, 'long': False, 'price': True, 'yr_built': True, 'zipcode': True},
    color_discrete_sequence=['teal'],
    opacity=0.4,
    zoom=8,
    center={'lat': dash_data['lat'].mean(), 'lon': dash_data['long'].mean()},
    mapbox_style="carto-darkmatter",
    custom_data=['price', 'yr_built', 'zipcode']
    
)

# Atualizando o layout do mapa
kc_map.update_layout(
    margin=dict(l=0, r=0, t=0, b=0),
    hovermode='closest',
    hoverlabel=dict(
        bgcolor="#343a40",
        font_size=13,
        font_family="Arial",
        bordercolor="black",
        font_color='white',
    )
    
)

kc_map.update_traces(
    marker=dict(size=(10)),
    hovertemplate="<b>%{hovertext}</b><br><br>" +
                  "<b>Price:</b> $%{customdata[0]:,.2f}<br>" +
                  "<b>Year Built</b>: %{customdata[1]}<br>" +
                  "<b>Zip Code:</b> %{customdata[2]}"
                  
)

# Exibindo o mapa
kc_map.show()


In [4]:
kc_hist = px.histogram(
    data_frame=dash_data,
    x="price",
    color_discrete_sequence=['teal'],
    nbins=30
)

kc_hist.update_layout(
    font=dict(color="white", family="Arial"),
    paper_bgcolor='#0c0c0c',
    plot_bgcolor='#0c0c0c',
    xaxis=dict(title='Price (bins)', color="white"),
    yaxis=dict(title='Frequency', color="white"),
    margin=dict(l=0, r=0, t=0, b=0),
    hoverlabel=dict(
        bgcolor="#343a40",
        font_size=13,
        font_family="Arial",
        bordercolor="black",
        font_color='white'
    )
)

kc_hist.update_traces(
    marker_line_color='black',
    marker_line_width=2,
    opacity=1,
    hovertemplate='<b>Bin: </b>%{x}<br><b>Frequency: </b>%{y}<extra></extra>'  
)

kc_hist.show()


In [5]:
kc_time_line = px.line(
    data_frame=dash_data['yr_built'].value_counts().sort_index(),
     color_discrete_sequence=['teal'],
     labels={'value': 'Count', 'yr_built': 'Year'}
)

kc_time_line.update_layout(
    font=dict(
        color="white",
        family="Arial"
    ),
    
    showlegend=False,
    margin=dict(l=0, r=0, t=0, b=0),
    paper_bgcolor='rgba(12, 12, 12, 0.9)',
    plot_bgcolor='rgba(12, 12, 12, 0.1)',
    
    xaxis=dict(
        nticks=12,
        color='white',
        showgrid=False),
    
    yaxis=dict(
        color='white',
        showgrid=False,
        linewidth=2
        ),
    
    hoverlabel=dict(
        bgcolor="#343a40",
        font_size=13,
        font_family="Arial",
        bordercolor="black",
        font_color='white'
    )
)

kc_time_line.update_traces(
    hovertemplate='<b>Year: </b>%{x}<br><b>Count: </b>%{y}<extra></extra>'  
)

kc_time_line.show()


#### Building Components

##### Dropdown 

In [377]:
dd_label_style = {
    'color': 'white',
    'font-size': 20,
    'background-color': '#2a2e32',
    'font-weight': 'bold',
    'width': '100%',
    'text-align': 'left'
}

dd_style = {
    'color': 'white',
    'background-color': '#2a2e32',
    'font-size': '20px',
    'height': '50px',
    'textAlign': 'center',
    'border-color': '#2a2e32',
    'margin': '0px'
}

city_label_options = list(dash_data.city.unique())
city_label_options.append('All')
city_value_options = city_label_options

floors_label_options = list(dash_data.floors.unique())
floors_label_options.append('All')
floors_value_options = floors_label_options

views_label_options = ['Nothing View'] + sorted(dash_data.view.unique())[1:] + ['All']
views_value_options = sorted(dash_data.view.unique()) + ['All']

wf_label_options = ['Without', 'With', 'Both']
wf_value_options = sorted(dash_data.waterfront.unique())
wf_value_options.append('All')


dd_city_options = [
     {
        'label': html.Span([label.upper()], style=dd_label_style),
        'value': value
    }
     
     for label, value in zip(city_label_options, city_value_options)
]

dd_floors_options = [
     {
        'label': html.Span([str(label).upper()], style=dd_label_style),
        'value': value
    }
     
     for label, value in zip(floors_label_options, floors_value_options)
]

dd_views_options = [
     {
        'label': html.Span([str(label).upper()], style=dd_label_style),
        'value': value
    }
     
     for label, value in zip(views_label_options, views_value_options)
]

dd_wf_options = [
    {
        'label': html.Span([label.upper()], style=dd_label_style),
        'value': value
    }
    
    for label, value in zip(wf_label_options, wf_value_options)
]

In [383]:
dd_city = dcc.Dropdown(
    id='dd-city',
    options=dd_city_options,
    value='All',
    clearable=False,
    maxHeight=150, 
    optionHeight=50,
    style=dd_style
)

dd_floors = dcc.Dropdown(
    id='dd-floors',
    options=dd_floors_options,
    value='All',
    clearable=False,
    maxHeight=150, 
    optionHeight=50,
    style=dd_style 
)

dd_views = dcc.Dropdown(
    id='dd-views',
    options=dd_views_options,
    value='All',
    clearable=False,
    maxHeight=150, 
    optionHeight=50,
    style=dd_style 
)

dd_waterfront = dcc.Dropdown(
    id='dd-waterfront',
    options=dd_wf_options,
    value='All',
    clearable=False,
    maxHeight=150, 
    optionHeight=50,
    style=dd_style
)                                      

#### Building Layout

In [385]:

app = Dash(__name__, external_stylesheets=[dbc.themes.BOOTSTRAP])

app.layout = html.Div(
    children=[
        dbc.NavbarSimple(
            brand='SEATLE HOUSE PRICE ANALYTICS',
            brand_style={'fontSize': '40px'},
            brand_href="#",
            color="dark",
            dark=True,
            children=[
                    dbc.NavItem(dbc.NavLink("Seatle Map", href="#")), 
                    dbc.NavItem(dbc.NavLink("Seatle Stats", href="#")), 
                    dbc.NavItem(dbc.NavLink("Compare Houses", href="#"))  
                ]
            ),
        
        html.Div(
            children=[
                dbc.Container(
                    fluid=True,
                    children=[
                        dbc.Row(
                            children=[
                                dbc.Col(
                                    children=[
                                        html.Div(
                                            children=[
                                                html.Label(
                                                    'CITY',
                                                    style={
                                                        'color': '#D3D3D3',
                                                        'background-color': '#2a2e32'
                                                    }
                                                ),
                                                dd_city
                                            ],
                                            style={
                                                'background-color': '#2a2e32'
                                            }
                                        )
                                    ],
                                    width=3,
                                    style={ 
                                        'background-color': '#2a2e32',
                                        'border-right': '0.5px solid #D3D3D3',
                                        'border-left': '0.5px solid #2a2e32',
                                        'border-bottom': '6px solid rgba(26, 26, 26, 0.3)',
                                        'border-top': '0.5px solid #2a2e32'
                                    }
                                ),
                                
                                dbc.Col(
                                    children=[
                                        html.Div(
                                            children=[
                                                html.Label(
                                                    'FLOORS',
                                                    style={
                                                        'color': '#D3D3D3',
                                                        'background-color': '#2a2e32'
                                                    }
                                                ),
                                                dd_floors
                                            ],
                                            style={
                                                'background-color': '#2a2e32'
                                            } 
                                        )
                                    ],
                                    width=3,
                                    style={
                                        'background-color': '#2a2e32',
                                        'border-right': '0.5px solid #D3D3D3',
                                        'border-left': '0.5px solid #D3D3D3',
                                        'border-bottom': '6px solid rgba(26, 26, 26, 0.3)',
                                        'border-top': '0.5px solid #2a2e32'
                                    }
                                ),
                                
                                dbc.Col(
                                    children=[
                                        html.Div(
                                            children=[
                                                html.Label(
                                                    'VIEWS',
                                                    style={
                                                        'color': '#D3D3D3',
                                                        'background-color': '#2a2e32'
                                                    }
                                                ),
                                                dd_views
                                            ],
                                            style={
                                                'background-color': '#2a2e32',
                                            }
                                        )
                                    ],
                                    width=3,
                                    style={
                                        'background-color': '#2a2e32',
                                        'border-right': '0.5px solid #D3D3D3',
                                        'border-left': '0.5px solid #D3D3D3',
                                        'border-bottom': '6px solid rgba(26, 26, 26, 0.3)',
                                        'border-top': '0.5px solid #2a2e32'    
                                    }
                                ),
                                
                                dbc.Col(
                                    children=[
                                        html.Div(
                                            children=[
                                                html.Label(
                                                    'WATERFRONT STATUS',
                                                    style={
                                                        'color': '#D3D3D3',
                                                        'background-color': '#2a2e32'
                                                    }
                                                ),
                                                dd_waterfront
                                            ],
                                            style={
                                                'background-color': '#2a2e32', 
                                            }
                                        )
                                    ],
                                    width=3,
                                    style={
                                        'background-color': '#2a2e32',
                                        'border-right': '0.5px solid #2a2e32',
                                        'border-left': '0.5px solid #D3D3D3',
                                        'border-bottom': '6px solid rgba(26, 26, 26, 0.3)',
                                        'border-top': '0.5px solid #2a2e32'
                                    
                                    }
                                ),
                            ]
                        ),
                        html.Div(
                            children=[
                                dbc.Row(
                                    children=[
                                        dbc.Col(
                                            children=[
                                                html.Label(
                                                    f'Houses found: {dash_data.shape[0]}',
                                                     style={
                                                        'font-size': '20px',
                                                        'height': '50px',
                                                        'color': 'white',
                                                        'background-color': '#343a40'       
                                                    }
                                                )
                                            ],
                                            width=3,
                                            style={
                                                'background-color': '#343a40',
                                                'border-style': 'solid',
                                                'border-color': '#D3D3D3',
                                                'border-width': '0.5px'
                                            }
                                        )
                                    ],
                                )                         

                            ],
                            style={'margin': '20px'}
                        ),
                        
                        html.Div(
                            children=[
                                dbc.Row(
                                    children=[
                                        dbc.Col(
                                            children=[
                                                dcc.Graph(
                                                    id='kc-map',
                                                    figure=kc_map,
                                                    config={'displayModeBar': False}
                                                )
                                            ],
                                            width=12
                                        )
                                    ]
                                )
                            ],
                            style={'margin': '20px'}
                        ),
                        
                        html.Div(
                            children=[
                                dbc.Row(
                                    children=[
                                        dbc.Col(
                                            children=[
                                                dcc.Graph(
                                                    id='kc-hist',
                                                    figure=kc_hist,
                                                    config={'displayModeBar': False}
                                                )
                                            ],
                                            width=12
                                        )
                                    ]
                                ),  
                            ],
                            style={'margin': '20px'}
                        ) 
                    ],
                    style={
                        'width': '80%',
                        'border': '0px solid teal',
                        'background-color': '#343a40',
                        'box-shadow': '0 0 8px teal'
                    }
                )
            ]
        )
    ],
    style={'background-color': '#1a1a1a', 'width': '100%', 'height': '100%'}
)


if __name__ == '__main__':
    app.run_server(debug=False)


In [ ]:
app = Dash(__name__, external_stylesheets=[dbc.themes.BOOTSTRAP])

app.layout = html.Div(className='main', children=[
    
    # Navbar
    dbc.NavbarSimple(
        brand='SEATLE HOUSE PRICE ANALYTICS',
        brand_style={'fontSize': '25px', 'textAlign': 'left'},
        brand_href='#',
        color='dark',
        dark=True,
        style={'font-weight': 'bold', 'height': '100px'},  
        className='w-100',  
        children=[
            dbc.NavItem(dbc.NavLink("Seatle Map", href="#", className="nav-link-")), 
            dbc.NavItem(dbc.NavLink("Seatle Stats", href="#", className="nav-link-white")), 
            dbc.NavItem(dbc.NavLink("Compare Houses", href="#", className="nav-link-white"))  
        ]
    ),
]
    
    
    dbc.Container(fluid=True, style={"padding": "0px", 'border-style': 'ridge', 'border-color': 'teal', 'width': '80%'}, children=[
        dbc.Row([
            dbc.Col([
                dcc.Dropdown(options=cities, clearable=False, id='dd-cities', placeholder='Select a City', maxHeight=150, style={'color': 'black',  'background-color': '#343a40', 'font-size': '20px', 'height': '20px', 'z-index': '10'})
            ], width=3),
            
            dbc.Col([
                dcc.Dropdown(options=cities, clearable=False, id='a', placeholder='Select Floors', maxHeight=150, style={'color': 'black',  'background-color': '#343a40', 'font-size': '20px', 'height': '20px', 'z-index': '10'})
            ], width=3),
            
            dbc.Col([
                dcc.Dropdown(options=cities, clearable=False, id='b', placeholder='Select Views', maxHeight=150, style={'color': 'black',  'background-color': '#343a40', 'font-size': '20px', 'height': '20px', 'z-index': '10'})
            ], width=3),
        ]),
        dbc.Row([
            dbc.Col([
                dcc.Graph(id='kc-map', figure=kc_map, config={'displayModeBar': False})
            ], width=12)
        ]), 
        
        dbc.Row([
            dbc.Col([
                dcc.Graph(id='kc-hist', figure=kc_hist, config={'displayModeBar': False})
            ], width=12)
        ]),
        
    ])
])

if __name__ == '__main__':
    app.run_server(debug=True)


In [ ]:
app = Dash(__name__, external_stylesheets=external_stylesheets)

colors = {
    'background': '#0c0c0c',
    'text': 'white'
}

options = list(dash_data['condition'].unique())
options.append('All')

fig1 = px.scatter_mapbox(data_frame=dash_data,
                        #title='King County Map',
                        lat='lat',
                        lon='long',
                        hover_name='zipcode',
                        hover_data=['price', 'yr_built'],
                        color_discrete_sequence=['teal'],
                        opacity=0.5,
                        zoom=7, 
                        height=300,
                        center={'lat': dash_data['lat'].mean(), 'lon': dash_data['long'].mean()},
                        mapbox_style="carto-darkmatter"    
                    )

fig2 = px.histogram(dash_data, x="price", color_discrete_sequence=['teal'], nbins=30)

app.layout = html.Div(style={'backgroundColor': colors['background'], 'padding': '20px'},
                      children=[
                          html.H5(
                              children=[
                                  'House Sales in King County, USA by ',
                                  html.A(children=['Fábio Fiuza'], href='https://www.linkedin.com/in/fábio-fiúza-7846b2275/')
                                  ],
                              
                              style={
                                  'textAlign': 'left',
                                  'color': colors['text'],
                                  'font-weight': 'bold',
                                }
                              ),
                          
                          html.Hr(
                               style={
                                  'borderColor': colors['text'],
                                }),
                          
                          html.H4(
                              children=[
                                  'KING COUNTY, WASHINGTON HOUSE SALES DASHBOARD'
                              ],
                              
                              style={
                                  'textAlign': 'center',
                                  'color': '#1789b3',
                                  'font-weight': 'bold',   
                                }
                              ),
                          
                          html.Hr(
                            style={
                                'height': '3px',
                                'borderColor': '#1789b3',
                                'borderWidth': '6px',
                                'opacity': '0.5',
                                'backgroundColor': '#1789b3',
                                'width': '90%'
                                
                                
                            }),
                          
                          dcc.Dropdown(options, value='All', id='dropdown'),
                          
                          dcc.Graph(
                              id='king-county-map',
                              figure=fig1
                              ),
                          
                          dcc.Graph(
                              id='histogram',
                              figure=fig2
                          ),
                          
                          dcc.RadioItems(['All', 'With', 'Without'], value='All', inline=True, id='radio')
                          
                          ]
                      )


@app.callback(
    [Output('king-county-map', 'figure'), Output('histogram', 'figure')],
    [Input('dropdown', 'value'), Input('radio', 'value')]
)

def update_output(dropdown_value, radio_value):
    
    if dropdown_value == 'All':
        df = dash_data
        
    else:
        df = dash_data[dash_data['condition'] == dropdown_value]

    if radio_value == 'All':
        pass
        
    elif radio_value == 'With':
        df = df[df['waterfront'] == 1]  
        
    else:
        df = df[df['waterfront'] == 0] 
        
        
    fig1 = px.scatter_mapbox(data_frame=df,
                        #title='King County Map',
                        lat='lat',
                        lon='long',
                        hover_name='zipcode',
                        hover_data=['price', 'yr_built'],
                        color_discrete_sequence=['teal'],
                        opacity=0.5,
                        zoom=7, 
                        height=500,
                        center={'lat': df['lat'].mean(), 'lon': df['long'].mean()},
                        mapbox_style="carto-darkmatter"    
                    )

    fig1.update_layout(
        margin={"r":0,"t":0,"l":0,"b":0},
        plot_bgcolor=colors['background'],
        paper_bgcolor=colors['background'],
        font_color=colors['text']
        )
    
    fig2 = px.histogram(df, x="price", color_discrete_sequence=['teal'], nbins=30)
    
    fig2.update_layout(
        title=dict(text='Distribution of House Prices', font=dict(size=20)),
        font_color="white",
        title_font_family="Arial",
        title_font_color="#1789b3",
        paper_bgcolor='#0c0c0c',
        plot_bgcolor='#0c0c0c',
        xaxis_title='Price (bins)',
        yaxis_title="Frequency" 
    )
    
    fig2.update_traces(marker_line_color='black', marker_line_width=2, opacity=1)

    return fig1, fig2



if __name__ == '__main__':
    app.run_server(debug=True)


In [ ]:
import dash
from dash import dcc, html
import dash_bootstrap_components as dbc
import plotly.express as px
import pandas as pd

# Dados de exemplo para o gráfico
dash_data = pd.DataFrame({
    "lat": [47.60, 47.67, 47.71],
    "long": [-122.33, -122.39, -122.40],
    "zipcode": [98101, 98102, 98103],
    "price": [500000, 600000, 700000],
    "yr_built": [1990, 1985, 2000]
})

# Criar o gráfico com Plotly Express
fig = px.scatter_mapbox(
    data_frame=dash_data,
    title='King County Map',
    lat='lat',
    lon='long',
    hover_name='zipcode',
    hover_data={'lat': False, 'long': False, 'price': True, 'yr_built': True},
    color_discrete_sequence=['teal'],
    opacity=0.5,
    zoom=7,
    center={'lat': dash_data['lat'].mean(), 'lon': dash_data['long'].mean()},
    mapbox_style="carto-darkmatter"
)

# Layout do Dash
app = dash.Dash(__name__, external_stylesheets=[dbc.themes.BOOTSTRAP])

app.layout = dbc.Container([
    # Cabeçalho
    dbc.NavbarSimple(
        brand="Meu Dashboard",
        brand_href="#",
        color="primary",
        dark=True,
        children=[
            dbc.NavItem(dbc.NavLink("Home", href="#")),
            dbc.NavItem(dbc.NavLink("Página 1", href="#")),
        ]
    ),
    # Conteúdo do dashboard
    dbc.Row([
        dbc.Col([
            html.H2("Gráfico do Mapa"),
            dcc.Graph(figure=fig)
        ])
    ], className="mt-4")
])

if __name__ == '__main__':
    app.run_server(debug=True)

In [ ]:
from dash import Dash, dcc, html, Input, Output

In [ ]:
interesting_houses['condition'] = interesting_houses['condition'].astype('object')

In [ ]:

external_stylesheets = ['https://codepen.io/chriddyp/pen/bWLwgP.css']

app = Dash(__name__, external_stylesheets=external_stylesheets)

app.layout = html.Div([
    html.H4('Análise de Correlação entre Features'),
    dcc.Dropdown(
        id="dropdown",
        options=['sqft_living', 'condition', 'grade', 'price'],
        value=['price', 'sqft_living'],
        multi=True
    ),
    dcc.Graph(id="graph"),
])


@app.callback(
    Output("graph", "figure"), 
    Input("dropdown", "value"))

def update_bar_chart(dims):
    fig = px.scatter(
        interesting_houses, 
        x=dims[0],
        y=dims[1],
        hover_name=interesting_houses.index,
        hover_data=['price', 'sqft_living', 'yr_built'],
        color='condition',
        size='sqft_living',
        log_x=False,
        size_max=20,
        color_discrete_map={
            1: '#29BEA9',
            2: '#00AEC0',
            3: '#0082D3',
            4: '#5A64C0',
            5: '#8A3F98'
        },
        
        category_orders={'condition': [5, 4, 3, 2, 1]},
        labels={
            'condition': 'Condition',
            'price': 'Price',
            'sqft_living': 'Sqft Living',
            'grade': 'Grade',
            'yr_built': 'Year Built'
        }
        )
    
    fig.update_layout(
        title=dict(text=f'{dims[0].capitalize()} X {dims[1].capitalize()}', font=dict(size=20), yref='paper'),
        font_family="Courier New",
        font_color="blue",
        title_font_family="Arial",
        title_font_color="red",
        legend_title_font_color="green",
    )
    

    
    return fig


app.run_server(mode='external')

In [ ]:
import plotly.express as px
import pandas as pd

# Dados fictícios para exemplo
data = {
    "City": ["New York", "Los Angeles", "Chicago"],
    "Lat": [40.7128, 34.0522, 41.8781],
    "Lon": [-74.0060, -118.2437, -87.6298],
}
df = pd.DataFrame(data)

# Mapa com os pontos das cidades
fig = px.scatter_mapbox(df, lat="Lat", lon="Lon", hover_name="City", zoom=3)

# Adicionando contorno (fronteiras) dos estados
fig.update_layout(mapbox_style="carto-positron")
fig.update_geos(
    visible=True, resolution=110, showcountries=True, countrycolor="Black", showsubunits=True, subunitcolor="Blue"
)

fig.show()


In [ ]:
df = px.data.iris()
df.species.un

In [ ]:
import pandas as pd

# Criando um DataFrame de exemplo
data = {
    'coluna_int64': [10, 20, 30, 40, 50],
    'outra_coluna': ['a', 'b', 'c', 'd', 'e']
}

df = pd.DataFrame(data)

# Exibindo o DataFrame antes da conversão
print("DataFrame antes da conversão:")
print(df.dtypes)

# Convertendo a coluna 'coluna_int64' para tipo 'object'
df['coluna_int64'] = df['coluna_int64'].astype('object')

# Exibindo o DataFrame depois da conversão
print("\nDataFrame depois da conversão:")
print(df.dtypes)

In [ ]:
from urllib.request import urlopen
import json

with urlopen('https://raw.githubusercontent.com/plotly/datasets/master/geojson-counties-fips.json') as response:
    counties = json.load(response)
    
fig = px.choropleth_mapbox(interesting_houses, geojson=counties, color='price')
fig.show()

In [ ]:
from dash import Dash, dcc, html, Input, Output
import plotly.express as px



app = Dash(__name__)

app.layout = html.Div([
    html.H4('Polotical candidate voting pool analysis'),
    html.P("Select a candidate:"),
    dcc.Graph(id="graph"),
])




fig = px.choropleth_mapbox(
    interesting_houses, geojson=counties, color='price',
    center={"lat": 45.5517, "lon": -73.7073}, zoom=9,
    range_color=[0, 6500])
fig.update_layout(
    margin={"r":0,"t":0,"l":0,"b":0})



app.run_server(debug=True)

In [ ]:

fig = px.histogram(das, x="price", color_discrete_sequence=['teal'], nbins=30)

fig.update_layout(
        title=dict(text='Distribution of House Prices', font=dict(size=20)),
        font_color="white",
        title_font_family="Arial",
        title_font_color="#1789b3",
        paper_bgcolor='#0c0c0c',
        plot_bgcolor='#0c0c0c',
        xaxis_title='Price (bins)',
        yaxis_title="Frequency" 
    )
fig.update_traces(marker_line_color='black', marker_line_width=2, opacity=1)
fig.show()

In [ ]:
px.histogram()

In [ ]:
interesting_houses.date.